# MUSEO VIRTUAL INTERACTIVO: ART AFTER DARK

#### Empezamos exportando datos de las APIs de Spotify y Lastfm

##### SPOTIPY:

In [ ]:
# Realizamos las instalaciones necesarias:

!pip install spotipy
!pip install mysql-connector
!pip install numpy

In [ ]:
# Importar librerías para manipulación y análisis de datos
import mysql.connector
from mysql.connector import errorcode
import requests
import pandas as pd
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
import unicodedata

In [ ]:
#Claves autenticación sacadas de la API:

CLIENT_ID = 'dafc633ff1234c729436a85de692fd11'
CLIENT_SECRET = 'edfda61ac9034327ba7338273e2b6b1d'

In [ ]:
# Autenticación en Spotipy:

auth_manager = SpotifyClientCredentials(client_id=CLIENT_ID, client_secret=CLIENT_SECRET)
sp = spotipy.Spotify(auth_manager=auth_manager)

In [ ]:
# Extracción de datos de Spotipy seleccionando 5 años alternos (2008, 2012, 2016, 1018 y 2024), para poder ver la tendencia, y 4 generos a estudiar (pop, rock, reggaeton y rap), 
# centrandonos en los tracks:

genres = ['pop', 'rock', 'reggaeton', 'rap']


results = []
artistas = []

for year in range(2008,2025,4):
    for genre in genres:
        for i in range(0,251,50):
            results_genre = sp.search(q=f'genre:{genre} year:{year}-{year}', type='track,album', limit=50, offset=i)
            for item in results_genre['tracks']['items']:
                artistas.append(item['artists'][0]['name']) ## añado a la lista de artistas
                results.append({
                        'name_track': item['name'],
                        'name_artist': item['artists'][0]['name'],
                        'genre': genre, 
                        'type': item['type'], 
                        'year': item['album']['release_date'][:4],
                        'popularity': item['popularity'],
                        'total_tracks': item['album']['total_tracks'],
                        'disc_number': item['disc_number'],    
                        'duration_ms': item['duration_ms'],
                        'explicit': item['explicit'] })

len(results)

6000

In [ ]:
# Obtenemos muchos artistas duplicados, es por esto que aplicamos el siguinete código para limpiar los duplicados de artistas:

len(artistas)

6000

In [ ]:
# Convertimos nuestra lista a set, para eliminar duplicados, y la volvemos a convertir a lista:

artistas_unicos = list(set(artistas))

In [ ]:
# De esta manera conseguimos pasar de una lista de 6000 artistas con duplicados a una lista de 1507 que nos servirá para más adelante.

len(artistas_unicos)

1507

In [ ]:
# Mostramos uno de los tracks añadidos a la lista de 'results' para poder ver la estructura que ha quedado:

results[800]

{'name_track': 'La Calle No Miente',
 'name_artist': 'Ñengo Flow',
 'genre': 'reggaeton',
 'type': 'track',
 'year': '2008',
 'popularity': 16,
 'total_tracks': 24,
 'disc_number': 1,
 'duration_ms': 186106,
 'explicit': False}

In [ ]:
# Convertimos nuestra lista de 'results' a un DataFrame:

df_results = pd.DataFrame(results)
df_results

name_track         name_artist genre  \
0                   Un violinista en tu tejado             Melendi   pop   
1                                 Viva La Vida            Coldplay   pop   
2                        Tenía Tanto Que Darte        Nena Daconte   pop   
3                           Mi Estrella Blanca      Fondo Flamenco   pop   
4                             Física o química          Despistaos   pop   
...                                        ...                 ...   ...   
5995                          EPISODIO D'AMORE             Geolier   rap   
5996  Missin’ You Like This (Feat. Luke Combs)         Post Malone   rap   
5997                                   NO FEAR  Falling In Reverse   rap   
5998                               WHITE NIGHT         Jake Miller   rap   
5999                                  Sombrero              Blanco   rap   

       type  year  popularity  total_tracks  disc_number  duration_ms  \
0     track  2008          68            14            1       222720   
1     track  2008          90            10            1       242373   
2     track  2008          66            11            1       204560   
3     track  2008          66            14            1       278973   
4     track  2008          64            32            1       191826   
...     ...   ...         ...           ...          ...          ...   
5995  track  2024          71            21            1       196613   
5996  track  2024          67            18            1       222781   
5997  track  2024          62            11            1       228823   
5998  track  2024          60             5            1       138755   
5999  track  2024          60            13            1       156794   

      explicit  
0        False  
1        False  
2        False  
3        False  
4        False  
...        ...  
5995     False  
5996     False  
5997      True  
5998     False  
5999      True  

[6000 rows x 10 columns]

In [ ]:
# Guardamos el DataFrame obtenido de Spotify:

df_results.to_csv("spotify.csv", index=0)

In [ ]:
# Abrimos el csv de Spotify que habíamos guardado:

df_spotify_csv = pd.read_csv("spotify.csv", index_col=0)

In [ ]:
# En el DataFrame aparecen tildes, símbolos y letras en mayúsculas que posteriormente nos pueden dar error en la inserción de datos a SQL, por esto hacemos el siguiente código:

diccionario_reemplazo = {'á': 'a',
    'à': 'a',
    'ä': 'a',
    'â': 'a',
    'ã': 'a',
    'é': 'e',
    'è': 'e',
    'ë': 'e',
    'ê': 'e',
    'í': 'i',
    'ì': 'i',
    'ï': 'i',
    'î': 'i',
    'ó': 'o',
    'ò': 'o',
    'ö': 'o',
    'ô': 'o',
    'õ': 'o',
    'ú': 'u',
    'ù': 'u',
    'ü': 'u',
    'û': 'u', 
    'ñ': 'n', 
    '$': 's'}

def limpiar_texto(texto):
    texto = texto.lower()
    for clave, valor in diccionario_reemplazo.items():
        texto = texto.replace(clave, valor)
    return texto

In [ ]:
# Corrección del df de spotify y guardado en nuevo CSV

df_spotify_csv['name_artist'] = df_spotify_csv['name_artist'].apply(limpiar_texto)
df_spotify_csv['name_track'] = df_spotify_csv['name_track'].apply(limpiar_texto)
df_spotify_csv.to_csv("spoty_min.csv", index=0)

In [ ]:
# Abrimos el csv de Spotify actualizado que hemos guardado:

df_spotify_csv = pd.read_csv("spoty_min.csv", index_col=False)

##### LAST FM:

In [ ]:
#Claves autenticación sacadas de la API:

API_KEY = '1e30864e52e175f6375a396feb368a48' 
BASE_URL = 'http://ws.audioscrobbler.com/2.0/'

In [ ]:
# Usamos la lista de artistas sin duplicados obtenida en Spotipy para sacar la información de la API de Lastfm:

artistas_unicos

artist_data = [] 
for artists in artistas_unicos:
    params_info = {
        'method': 'artist.getinfo',
        'artist': artists,
        'api_key': API_KEY,
        'format': 'json'
    }
    response_info = requests.get(BASE_URL, params=params_info)
    data_info = response_info.json()
    artist_data.append(data_info)
artist_data



[{'artist': {'name': 'Agnes',
   'mbid': 'fd157ff9-5a29-449a-a1df-c1ef27f84549',
   'url': 'https://www.last.fm/music/Agnes',
   'image': [{'#text': 'https://lastfm.freetls.fastly.net/i/u/34s/2a96cbd8b46e442fc41c2b86b821562f.png',
     'size': 'small'},
    {'#text': 'https://lastfm.freetls.fastly.net/i/u/64s/2a96cbd8b46e442fc41c2b86b821562f.png',
     'size': 'medium'},
    {'#text': 'https://lastfm.freetls.fastly.net/i/u/174s/2a96cbd8b46e442fc41c2b86b821562f.png',
     'size': 'large'},
    {'#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/2a96cbd8b46e442fc41c2b86b821562f.png',
     'size': 'extralarge'},
    {'#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/2a96cbd8b46e442fc41c2b86b821562f.png',
     'size': 'mega'},
    {'#text': 'https://lastfm.freetls.fastly.net/i/u/300x300/2a96cbd8b46e442fc41c2b86b821562f.png',
     'size': ''}],
   'streamable': '0',
   'ontour': '0',
   'stats': {'listeners': '460345', 'playcount': '7032763'},
   'similar': {'artist': [{'name': '

In [ ]:
# Intentamos sacar la información interesante iterando, pero nos daba error (no sabemos por qué :D), así que cambiamos el código.

artist_data[0]['artist']['name']
artist_data[0]['artist']['ontour']
artist_data[0]['artist']['stats']['playcount'] # reproducciones
artist_data[0]['artist']['stats']['listeners'] # oyentes
artist_data[0]['artist']['similar']['artist'][0]['name']
artist_data[0]['artist']['tags']['tag'][1]['name'] # género
artist_data[1]['artist']['bio']['summary']
artist_data[1]['artist']['bio']




{'links': {'link': {'#text': '',
   'rel': 'original',
   'href': 'https://last.fm/music/Soft+Play/+wiki'}},
 'published': '09 Feb 2023, 12:02',
 'summary': 'SOFT PLAY (formerly known as Slaves) are an English punk rock duo formed in Royal Tunbridge Wells in 2012, consisting of Isaac Holman (lead vocals, drums) and Laurie Vincent (backing vocals, guitar, bass). Their music has been described as "British punk with harsh bluesy garage riffs". <a href="https://www.last.fm/music/Soft+Play">Read more on Last.fm</a>',
 'content': 'SOFT PLAY (formerly known as Slaves) are an English punk rock duo formed in Royal Tunbridge Wells in 2012, consisting of Isaac Holman (lead vocals, drums) and Laurie Vincent (backing vocals, guitar, bass). Their music has been described as "British punk with harsh bluesy garage riffs". <a href="https://www.last.fm/music/Soft+Play">Read more on Last.fm</a>. User-contributed text is available under the Creative Commons By-SA License; additional terms may apply.'}

In [ ]:
# Con este código obtenemos la información que nos interesa de cada artista de Lastfm:

info_artists = []
for i in artist_data:
    artista = {'artista': i.get('artist', {}).get('name', 'no está'), 
               'de_gira': i.get('artist', {}).get('ontour', 'no está'),
               'reproducciones': i.get('artist', {}).get('stats', {}).get('playcount', 'no está'),
               'oyentes': i.get('artist', {}).get('stats', {}).get('listeners', 'no está'),
               'biografia': i.get('artist', {}).get('bio', {}).get('summary', 'no está'),
               'similares': [similar.get('name', 'no está') for similar in i.get('artist', {}).get('similar', {}).get('artist', [])], 
               'genero': [tag.get('name', 'no está') for tag in i.get('artist', {}).get('tags', {}).get('tag', [])]}
    info_artists.append(artista)

In [ ]:
# Convertimos nuestra lista de 'info_artists' a un DataFrame:

df_lastfm = pd.DataFrame(info_artists)
df_lastfm

artista de_gira reproducciones  oyentes  \
0                 Agnes       0        7032763   460345   
1             Olly Murs       1       20784130  1395662   
2     Funzo & Baby Loud       0        1041905    27206   
3         Calvin Harris       1      168259511  4369897   
4         Black Sabbath       1      166644160  3784184   
...                 ...     ...            ...      ...   
1502            Skillet       1       64933099  1870247   
1503           Gio Pika       1         788466    35776   
1504         Luis Fonsi       0       12921996  1157296   
1505        Deep Purple       1       70317367  2720169   
1506         Kchiporros       0         262540    10201   

                                              biografia  \
0      Agnes Carlsson (credited simply as Agnes), bo...   
1     Oliver Stanley "Olly" Murs (born May 14, 1984 ...   
2      <a href="https://www.last.fm/music/Funzo+&+Ba...   
3     Adam Richard Wiles, known professionally as Ca...   
4     Black Sabbath was an English heavy metal band ...   
...                                                 ...   
1502  Skillet is an American Christian rock band for...   
1503   <a href="https://www.last.fm/music/Gio+Pika">...   
1504  Luis Alfonso Rodríguez López-Cepero, more comm...   
1505  Deep Purple are an English rock band formed in...   
1506  Kchiporros es una banda originaria de Paraguay...   

                                              similares  \
0     [Loreen, Kylie Minogue, September, Dotter, Jes...   
1     [Take That, JLS, Ella Henderson, Rixton, The W...   
2     [Ayax y Prok, Cruz Cafuné, Alizzz, Paula Cende...   
3       [David Guetta, Avicii, Zedd, Alesso, Jax Jones]   
4     [Ozzy Osbourne, Dio, Heaven & Hell, Judas Prie...   
...                                                 ...   
1502  [Thousand Foot Krutch, Ashes Remain, Disciple,...   
1503  [Aigel, Nurminsky, Miyagi & Andy Panda, Egor K...   
1504  [David Bisbal, Reik, Pablo Alborán, Piso 21, A...   
1505  [Rainbow, Uriah Heep, UFO, Whitesnake, Black S...   
1506  [La De Roberto, Los Verduleros, Bohemia Urbana...   

                                                 genero  
0      [pop, dance, swedish, female vocalists, finnish]  
1       [pop, british, male vocalists, X factor, indie]  
2                        [urban, spain, trap, alicante]  
3        [electronic, dance, electro, Disco, seen live]  
4     [heavy metal, hard rock, classic rock, metal, ...  
...                                                 ...  
1502  [christian rock, alternative rock, rock, alter...  
1503                               [electronic, Russia]  
1504        [pop, latin, latin pop, Romantica, spanish]  
1505  [hard rock, classic rock, rock, Progressive ro...  
1506           [paraguay, punk rock, cumbia, punk, ska]  

[1507 rows x 7 columns]

In [ ]:
# Guardamos el DataFrame obtenido de Lastfm:

df_lastfm.to_csv("lastfm.csv", index=0)

In [ ]:
# Abrimos el csv de Lastfm que habíamos guardado:

df_lastfm_csv = pd.read_csv("lastfm.csv", index_col=0)

In [ ]:
# Igual que nos pasó con Spotify, en el DataFrame aparecen tildes, símbolos y letras en mayúsculas que posteriormente nos pueden dar error en la inserción de datos a SQL, 
# por esto volvemos a aplicar la función creada anteriormente, corrigiendo el df de Lasfm y guardándolo en un nuevo csv:

df_lastfm_csv['artista'] = df_lastfm_csv['artista'].apply(limpiar_texto)
df_lastfm_csv['similares'] = df_lastfm_csv['similares'].apply(limpiar_texto)
df_lastfm_csv['genero'] = df_lastfm_csv['genero'].apply(limpiar_texto)
df_lastfm_csv.to_csv("lastfm_min.csv", index=0)


In [ ]:
# Abrimos el csv de Lastfm actualizado que hemos guardado:

df_lastfm_csv = pd.read_csv("lastfm_min.csv", index_col=False)

In [ ]:
# Además encontramos que en el df de Lastfm, aparece 1 artista duplicado. Así que para eliminar uno de los registros duplicados conociendo la posición (648 y 887 iguales), 
# hacemos lo siguiente:

df_lastfm_csv.drop(index=887, inplace=True)

In [ ]:
# En el df de Lastfm, aparecen dos columnas con varios datos dentro de cada una (similares y genero). Así que para normalizar los datos, creamos una tabla a parte para cada columna 
# relacionandolas con los artistas.

#ARTISTAS SIMILARES:
last_list = df_lastfm_csv.values.tolist()
similares = []
for artist in last_list: 
    art_sim = artist[6].replace("[", "").replace("]", "").replace("'", "").split(', ')
    for similar in art_sim:
        similares.append([artist[0], similar])
        
df_similar = pd.DataFrame(similares, columns = ['artist','similar_artist'])
df_similar.to_csv("puente_artist_similar.csv", index=0)

#GENEROS:
genres_list = df_lastfm_csv.values.tolist()
generos = []
for artist in genres_list: 
    genre = artist[6].replace("[", "").replace("]", "").replace("'", "").split(', ')
    for g in genre:
        generos.append([artist[0], g])
        
df_genre = pd.DataFrame(generos, columns = ['artist','genre'])
df_genre.to_csv("puente_genres.csv", index=0)

In [ ]:
# Limpieza de las columnas de similares y generos de lastfm y sustitución código con regex
 
diccionario_reemplazo = {'[': '',
    ']': '',
    "'": ''}

def limpiar_texto(texto):
    texto = texto.lower()
    for clave, valor in diccionario_reemplazo.items():
        texto = texto.replace(clave, valor)
    return texto

df_lastfm_csv['similares'] = df_lastfm_csv['similares'].apply(limpiar_texto)
df_lastfm_csv['genero'] = df_lastfm_csv['genero'].apply(limpiar_texto)
df_lastfm_csv['biografia'] = df_lastfm_csv['biografia'].str.replace(r'<a href="https://www\.last\.fm/music/[^>]+">Read more on Last\.fm</a>', '', regex=True)

df_lastfm_csv.to_csv("lastfm_min2.csv", index=0)